# Analise de Vagas

## Imports

In [2]:
import requests
import json
import pandas as pd
from bs4 import BeautifulSoup
import string
from difflib import SequenceMatcher 

## Funções

In [11]:
def getSoup(url):
  payload={}
  headers = {
    'User-Agent': 'Mozilla/5.0'
  }

  html = requests.get(url).content
  soup = BeautifulSoup(html, 'html.parser')
  
  return soup

def similar(str1, str2): 
    return SequenceMatcher(None, str1, str2).ratio() 

def verificaPalavraEmGrupo(palavra, grupoAtual, grupos):
    for palavraChave in grupos[grupoAtual]:
        similaridade = similar(palavra.upper(), palavraChave.upper())
        if (similaridade >= 0.9):
            print(f"palavra: {palavra}; palavraChave: {palavraChave}; similaridade: {similaridade}")
            return True
    return False
    

## Obter cargos com maior número de vagas

### Obter link dos cargos

In [ ]:
cargoList = list()

soup = getSoup("https://www.vagas.com.br/cargo/")
section = soup.find("section", {"class": "conteudo"})
for a in section.find_all('a', href=True):
  cargoList.append(a['href'])

### Navegar por cargos

In [ ]:
listCargos = list()
dictCargo = dict()
for cargo in cargoList:
  try:
    soup = getSoup(cargo)
    link = soup.find('a', {'class': 'button outline'})['href']
    soupCargo = getSoup(link)
    tituloCargo = soupCargo.find('div', {'class': 'titulo-cargo'})
    quantidadeVagas = soupCargo.find('h1')
    if tituloCargo == None or quantidadeVagas == None:
      continue

    dictCargo = {'Cargo': tituloCargo.text.split('Saiba mais')[0].strip(), 'Vagas': quantidadeVagas.text.split(' ')[0].strip(), 'Link': link}
    listCargos.append(dictCargo.copy())

    print(dictCargo)
  except:
    print("Não foi possível obter dados")

{'Cargo': 'Abertura de Contas', 'Vagas': '44', 'Link': 'https://www.vagas.com.br/vagas-de-abertura-de-contas'}
{'Cargo': 'Acabador', 'Vagas': '134', 'Link': 'https://www.vagas.com.br/vagas-de-acabador'}
{'Cargo': 'Acabamento', 'Vagas': '134', 'Link': 'https://www.vagas.com.br/vagas-de-acabamento'}
{'Cargo': 'Acadêmico Bolsista', 'Vagas': '1', 'Link': 'https://www.vagas.com.br/vagas-de-acadêmico-bolsista'}
{'Cargo': 'Acadêmico de Enfermagem', 'Vagas': '25', 'Link': 'https://www.vagas.com.br/vagas-de-acadêmico-de-enfermagem'}
{'Cargo': 'Account', 'Vagas': '20', 'Link': 'https://www.vagas.com.br/vagas-de-account'}
{'Cargo': 'Account Manager', 'Vagas': '4', 'Link': 'https://www.vagas.com.br/vagas-de-account-manager'}
{'Cargo': 'Acompanhante', 'Vagas': '66', 'Link': 'https://www.vagas.com.br/vagas-de-acompanhante'}
{'Cargo': 'Acompanhante Comunitário', 'Vagas': '8', 'Link': 'https://www.vagas.com.br/vagas-de-acompanhante-comunitário'}
{'Cargo': 'Acompanhante de Idoso', 'Vagas': '1', 'Link':

### Salvar cargos em arquivo CSV

In [ ]:
df = pd.DataFrame.from_dict(listCargos)
df.to_csv(r'AnaliseDeCargos.csv', index = False, header=True)

## Obter detalhes de vagas

### Definir lista de cargos

In [14]:
listProfissoes = []
listProfissoes.append("programador")

### Navegar pelos link de vagas

In [15]:
pagina = 1
vagaList = list()

for profissao in listProfissoes:
  while True:
    url = f"https://www.vagas.com.br/vagas-de-{profissao}?&q={profissao}&pagina={pagina}&_=1666241769285"

    print(f"URL: {url}")
    soup = getSoup(url)
    div = soup.find(id="todasVagas")


    #print(f"Valor de Div = {div}")
    if (div == None):
      break

    for a in div.find_all('a', href=True):
      vagaList.append(a['href'])
    pagina += 1


print(pagina)
for vaga in vagaList:
  print(vaga)

URL: https://www.vagas.com.br/vagas-de-programador?&q=programador&pagina=1&_=1666241769285
URL: https://www.vagas.com.br/vagas-de-programador?&q=programador&pagina=2&_=1666241769285
URL: https://www.vagas.com.br/vagas-de-programador?&q=programador&pagina=3&_=1666241769285
URL: https://www.vagas.com.br/vagas-de-programador?&q=programador&pagina=4&_=1666241769285
URL: https://www.vagas.com.br/vagas-de-programador?&q=programador&pagina=5&_=1666241769285
URL: https://www.vagas.com.br/vagas-de-programador?&q=programador&pagina=6&_=1666241769285
URL: https://www.vagas.com.br/vagas-de-programador?&q=programador&pagina=7&_=1666241769285
URL: https://www.vagas.com.br/vagas-de-programador?&q=programador&pagina=8&_=1666241769285
URL: https://www.vagas.com.br/vagas-de-programador?&q=programador&pagina=9&_=1666241769285
URL: https://www.vagas.com.br/vagas-de-programador?&q=programador&pagina=10&_=1666241769285
URL: https://www.vagas.com.br/vagas-de-programador?&q=programador&pagina=11&_=16662417692

### Obter descricao de vaga

In [18]:
descricaoVagaDict = dict()
descricaoVagaList = list()

for vaga in vagaList:
  try:
    soupVaga = getSoup("https://www.vagas.com.br" + vaga)
    tituloVaga = soupVaga.find("h1").text.strip()
    descricaoVaga = soupVaga.find("div", {"class": "job-tab-content job-description__text texto"}).text.strip()

    descricaoVagaDict["Titulo"] = tituloVaga
    descricaoVagaDict["Descricao"] = descricaoVaga

    descricaoVagaList.append(descricaoVagaDict.copy())
    print(descricaoVagaDict)
  except:
    print("Não foi possível obter vaga")


{'Titulo': 'Programador Progress Sr', 'Descricao': 'Descrição\nDescrição: Principais atividades:\xa0· Proceder a codificação dos programas de computador, estudando os objetivos propostos, analisando as características dos dados de entrada e o processamento necessário a obtenção dos dados de saída desejados;\xa0· Elaborar estudos sobre a criação e alteração de metodologias e procedimentos necessários ao desenvolvimento dos programas;\xa0· Realizar testes em condições operacionais simuladas, visando verificar se o programa executa corretamente dentro do especificado e com a performance adequada;\xa0· Realizar simulações e criar ambientes de produção a fim de aferir os resultados dos programas; entre outras atividades.Outros requisitos: Requisitos:· Superior completo em Sistemas de Informação, Ciência da Computação ou Engenharia da Computação; · Sólidos conhecimentos em Progress 4GL, templates do TOVS Datasul, integrações utilizando API´S e versionamento; · Desejável Conhecimentos em TOTV

### Salvar detalhes das vaga em arquivo CSV

In [25]:
df = pd.DataFrame.from_dict(descricaoVagaList)
df.to_csv(r'drive/MyDrive/FTT/TCC/AnaliseDeVagas_Programador.csv', index = False, header=True)

## Definir valores dos Centros de Ciências correlacionados ao Cargo

### Definição das palavras chave do Centro de Ciências

In [26]:
educacao = ["Educação", "Artes", "Letras", "Pedagogia"]
saude = ["Saúde", "Educação Física", "Enfermagem", "Farmácia", "Fisioterapia", "Licenciatura em Educação Física", "Medicina", "Medicina Veterinária", "Veterinária", "Nutrição", "Odontologia", "Psicologia"]
exatasNaturais = ["Exatas", "Naturais", "Ciência da Computação", "Computação", "Ciências Biológicas", "Biológicas", "Licenciatura em Computação", "Matemática", "Química", "Sistemas de Informação"]
humanasComunicacao = ["Humanas", "Comunicação", "Ciências da Religião", "Religião", "Ciências Sociais", "Comunicação Social", "Sociais", "História", "Moda", "Secretáriado Executivo Bilíngue", "Serviço Social"]
cienciasJuridicas = ["Ciências Jurídicas", "Jurídicas", "Direito"]
cienciasSociaisAplicadas = ["Ciências Sociais Aplicadas", "Administração", "Ciências Contábeis", "Contábeis", "Ciências Econômicas", "Econômicas", "Tecnologia em Marketing", "Marketing", "Turismo", "Lazer"]
cienciasTecnologicas = ["Ciências Tecnológicas", "Tecnológicas", "Arquitetura", "Urbanismo", "Design", "Engenharia", "Engenharia Civil", "Engenharia de Produção", "Engenharia de Telecomunicações", "Engenharia Elétrica", "Engenharia Florestal", "Engenharia Química", "Tecnologia em Processos Industriais", "Processos Industriais"]

grupos = {"educacao": educacao, "saude": saude, "exatasNaturais": exatasNaturais, "humanasComunicacao": humanasComunicacao, "cienciasJuridicas": cienciasJuridicas, "cienciasSociaisAplicadas": cienciasSociaisAplicadas, "cienciasTecnologicas": cienciasTecnologicas}

print(grupos)

{'educacao': ['Educação', 'Artes', 'Letras', 'Pedagogia'], 'saude': ['Saúde', 'Educação Física', 'Enfermagem', 'Farmácia', 'Fisioterapia', 'Licenciatura em Educação Física', 'Medicina', 'Medicina Veterinária', 'Veterinária', 'Nutrição', 'Odontologia', 'Psicologia'], 'exatasNaturais': ['Exatas', 'Naturais', 'Ciência da Computação', 'Computação', 'Ciências Biológicas', 'Biológicas', 'Licenciatura em Computação', 'Matemática', 'Química', 'Sistemas de Informação'], 'humanasComunicacao': ['Humanas', 'Comunicação', 'Ciências da Religião', 'Religião', 'Ciências Sociais', 'Comunicação Social', 'Sociais', 'História', 'Moda', 'Secretáriado Executivo Bilíngue', 'Serviço Social'], 'cienciasJuridicas': ['Ciências Jurídicas', 'Jurídicas', 'Direito'], 'cienciasSociaisAplicadas': ['Ciências Sociais Aplicadas', 'Administração', 'Ciências Contábeis', 'Contábeis', 'Ciências Econômicas', 'Econômicas', 'Tecnologia em Marketing', 'Marketing', 'Turismo', 'Lazer'], 'cienciasTecnologicas': ['Ciências Tecnológi

### Ler Arquivo CSV do Cargo

In [31]:
administrador = pd.read_csv('./drive/MyDrive/FTT/TCC/AnaliseDeVagas_Administrador.csv')

### Definir lista de palavras por vaga

In [32]:
dicionarioPalavraVaga = dict()
listaVagas = list()

descricoes = administrador['Descricao']

for vaga in administrador.to_dict('records'):
    listaPalavrasVaga = list()
    descricao = vaga['Descricao']
    titulo = vaga['Titulo']
    for palavra in descricao.split(' '):
        palavra = palavra.translate(str.maketrans('', '', string.punctuation)).strip()
        listaPalavrasVaga.append(palavra)
    dicionarioPalavraVaga['Titulo'] = titulo
    dicionarioPalavraVaga['Palavras'] = listaPalavrasVaga.copy()
    listaVagas.append(dicionarioPalavraVaga.copy())
    listaPalavrasVaga.clear()


### Definir atributos com base nos Centros de Ciência para as vagas

In [33]:
listaVagasComAtributos = list()

for vaga in listaVagas:
    atributos = {"educacao": 0, "saude": 0, "exatasNaturais": 0, "humanasComunicacao": 0, "cienciasJuridicas": 0, "cienciasSociaisAplicadas": 0, "cienciasTecnologicas": 0}
    for palavra in vaga['Palavras']:
        for grupo in grupos: 
            if (verificaPalavraEmGrupo(palavra, grupo, grupos)):
                atributos[grupo] = 1
    vaga['atributos'] = atributos.copy()
    listaVagasComAtributos.append(vaga.copy())

A saída de streaming foi truncada nas últimas 5000 linhas.
palavra: Engenharias; palavraChave: Engenharia; similaridade: 0.9523809523809523
palavra: Administração; palavraChave: Administração; similaridade: 1.0
palavra: Engenharia; palavraChave: Engenharia; similaridade: 1.0
palavra: jurídica; palavraChave: Jurídicas; similaridade: 0.9411764705882353
palavra: Enfermagem; palavraChave: Enfermagem; similaridade: 1.0
palavra: Enfermagem; palavraChave: Enfermagem; similaridade: 1.0
palavra: enfermagem; palavraChave: Enfermagem; similaridade: 1.0
palavra: Enfermagem; palavraChave: Enfermagem; similaridade: 1.0
palavra: enfermagem; palavraChave: Enfermagem; similaridade: 1.0
palavra: educação; palavraChave: Educação; similaridade: 1.0
palavra: comunicação; palavraChave: Comunicação; similaridade: 1.0
palavra: contábeis; palavraChave: Contábeis; similaridade: 1.0
palavra: contábeis; palavraChave: Contábeis; similaridade: 1.0
palavra: econômicos; palavraChave: Econômicas; similaridade: 0.9
pal

### Agrupamento dos resultados

In [34]:
grupoValores = dict()
for grupo in grupos:
    grupoValores[grupo] = 0
for grupo in grupos:
    for vaga in listaVagasComAtributos:
        valor = vaga['atributos'][grupo]
        grupoValores[grupo] += valor

print(grupoValores)

{'educacao': 121, 'saude': 477, 'exatasNaturais': 148, 'humanasComunicacao': 660, 'cienciasJuridicas': 165, 'cienciasSociaisAplicadas': 1909, 'cienciasTecnologicas': 711}
